In [ ]:
workdir = "/content/drive/MyDrive/QA_pt"
%mkdir {workdir}
!export HF_DATASETS_CACHE="{workdir}/cache_huggingface"

cache_dir=f"{workdir}/cache_huggingface"

%cd {workdir}

!apt update -y
!apt install -y enchant libenchant-dev  hunspell-pt-br
!pip install pyenchant datasets

/content/drive/MyDrive/QA_pt
Get:1 http://security.ubuntu.com/ubuntu bionic-security InRelease [88.7 kB]
Get:2 https://cloud.r-project.org/bin/linux/ubuntu bionic-cran40/ InRelease [3,626 B]
Ign:3 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  InRelease
Hit:4 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  InRelease
Hit:5 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  Release
Get:6 http://ppa.launchpad.net/c2d4u.team/c2d4u4.0+/ubuntu bionic InRelease [15.9 kB]
Hit:7 http://archive.ubuntu.com/ubuntu bionic InRelease
Get:8 http://archive.ubuntu.com/ubuntu bionic-updates InRelease [88.7 kB]
Hit:9 http://ppa.launchpad.net/cran/libgit2/ubuntu bionic InRelease
Hit:10 http://ppa.launchpad.net/deadsnakes/ppa/ubuntu bionic InRelease
Get:11 http://archive.ubuntu.com/ubuntu bionic-backports InRelease [83.3 kB]
Hit:12 http://ppa.launchpad.net/graphics-drivers/ppa/ubuntu bionic InRelease
Ge

In [ ]:
from datasets import load_dataset
import enchant
import re

def is_portuguese(text: str) -> bool:
  words = re.split(r'\s', text)
  words = [w for w in words if w.isalpha()]
  pt_words = [w for w in words if spell.check(w)]

  return len(pt_words) >= 3

spell = enchant.Dict("pt_BR")

In [ ]:
all_data = load_dataset("clips/mqa", language="pt", cache_dir=cache_dir)
filtered_data = all_data.filter(lambda example: '?' in example['name'] and is_portuguese(example['name']))

Generating train split: 0 examples [00:00, ? examples/s]

Dataset mqa downloaded and prepared to /content/drive/MyDrive/QA_pt/cache_huggingface/clips___mqa/pt-all-question-language=pt/0.0.0/7eda4cdcbd6f009259fc516f204d776915a5f54ea2ad414c3dcddfaacd4dfe0b. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Dataset mqa downloaded and prepared to /content/drive/MyDrive/QA_pt/cache_huggingface/clips___mqa/pt-faq-question-language=pt,scope=faq/0.0.0/7eda4cdcbd6f009259fc516f204d776915a5f54ea2ad414c3dcddfaacd4dfe0b. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Dataset mqa downloaded and prepared to /content/drive/MyDrive/QA_pt/cache_huggingface/clips___mqa/pt-cqa-question-language=pt,scope=cqa/0.0.0/7eda4cdcbd6f009259fc516f204d776915a5f54ea2ad414c3dcddfaacd4dfe0b. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
COLUMNS = [
    'id',
    'domain',
    'bucket',
    'question_title',
    'question_text',
    'answer_title',
    'answer_text',
    'is_accepted',
]

def format(data):
  prepro_data = {column: list() for column in COLUMNS}

  for question_idx in range(len(data['id'])):

    for answer_idx, answer in enumerate(data['answers'][question_idx]):
      prepro_data['id'].append(data['id'][question_idx] + '-' + str(answer_idx))


      for column in ['domain', 'bucket']:
        prepro_data[column].append(data[column][question_idx])

      prepro_data['question_title'].append(data['name'][question_idx])
      prepro_data['question_text'].append(data['text'][question_idx])
      prepro_data['answer_title'].append(answer['name'])
      prepro_data['answer_text'].append(answer['text'])
      prepro_data['is_accepted'].append(answer['is_accepted'])
  
  return prepro_data

prepro_data = filtered_data.map(
    format,
    batched=True,
    remove_columns=[
        'text',
        'name',
        'answers',
    ]
)

  0%|          | 0/5477 [00:00<?, ?ba/s]

In [ ]:
prepro_data.save_to_disk('prepro_data')

In [ ]:
df = prepro_data['train'].to_pandas()
df.to_csv('QA_PT.tsv', sep='\t', index=None)

In [ ]:
%ls

cache_huggingface/  prepro_data/  QA_PT.tsv


In [ ]:
import pandas as pd

df = pd.read_table('QA_PT.tsv', lineterminator='\n')

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:3326: DtypeWarning: Columns (4,5) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [ ]:
columns = [
    "question_title",
    "question_text",
    "answer_title",
    "answer_text",
    "is_accepted"
]

df[columns]

question_title  \
0                                      o que é um arranjo?   
1        qual a quantidade de vezes que o shih tzu tem ...   
2        o que eu posso dar para o shih tzu comer além ...   
3            qual é a melhor marca de ração para shih tzu?   
4                como dar ração para filhotes de shih tzu?   
...                                                    ...   
5753875  No Stimulsoft o @CAMPO(campo) só pode ser util...   
5753876  Como alterar o valor do progresso de um proces...   
5753877  No Builder, para que serve os campos "Herdar d...   
5753878  Existe algum método que retorne o arquivo do B...   
5753879  Quais os package sources preciso incluir no Vi...   

                                             question_text answer_title  \
0                                                      NaN          NaN   
1                                                      NaN          NaN   
2                                                      NaN          NaN   
3                                                      NaN          NaN   
4                                                      NaN          NaN   
...                                                    ...          ...   
5753875  Seria possível criar uma variável qualquer par...          NaN   
5753876  Tenho um BusinessComponent que executa um proc...          NaN   
5753877  No Builder, para que serve os campos "Herdar d...          NaN   
5753878  Preciso realizar uma rotina que irá ler vários...          NaN   
5753879  Quero compilar o BEF. Quais os servidores nuge...          NaN   

                                               answer_text  is_accepted  
0        um arranjo é onde as pessoas são diretas umas ...         True  
1        a quantidade de vezes que um shih tzu deve com...         True  
2        É indicado que a alimentação de um cachorro se...         True  
3        dentre quais as melhores rações para shih tzu ...         True  
4        a oferta da ração para um shih tzu filhote var...         True  
...                                                    ...          ...  
5753875  Para "pegar" o valor do campo (sem ser no SQL ...        False  
5753876  A classe ProcessLog é indicado para realizar  ...         True  
5753877  Serve para herdar campos de uma tabela relacio...         True  
5753878  Utilize a classe Benner.Tecnologia.Common.File...         True  
5753879  Seriam esses:\n\n\nNuget Benner: <http://desen...         True  

[5753880 rows x 5 columns]

In [ ]:
df['question_text'].isna().value_counts()

True     5332276
False     421604
Name: question_text, dtype: int64

In [ ]:
df['answer_title'].isna().value_counts()

True     5753502
False        378
Name: answer_title, dtype: int64

In [ ]:
(~df['answer_title'].isna() & ~df['question_text'].isna()).value_counts()

False    5753784
True          96
dtype: int64

In [ ]:
df['is_accepted'].value_counts()

True     5376445
False     377435
Name: is_accepted, dtype: int64

In [ ]:
from datasets import load_from_disk

data = load_from_disk('prepro_data')

In [ ]:
data

DatasetDict({
    train: Dataset({
        features: ['id', 'domain', 'bucket', 'question_title', 'question_text', 'answer_title', 'answer_text', 'is_accepted'],
        num_rows: 5753880
    })
})